In [34]:
from ngsolve import *
from netgen.occ import *
from ngsolve.webgui import Draw

import numpy as np
import matplotlib.pyplot as plt

import pickle

maxh = 0.1

inner = Circle((0.0, 0.0), 1).Face()
inner.faces.name = 'inner'

outer = Circle((0.0, 0.0), 2).Face()
outer = outer - inner

geo = Glue([inner, outer])
mesh = Mesh(OCCGeometry(geo, dim=2).GenerateMesh(maxh=maxh))

# No issue if the below two lines are commented out (i.e. refinement everywhere instead of only on inner) 
for el in mesh.Elements():
    mesh.SetRefinementFlag(el, el.mat == "inner")

mesh.Refine()

Draw(mesh)

gfvs = []

for _ in range(2):
    fes = H1(mesh, order = 2) # Does not happen for order = 1
    
    gf = GridFunction(fes)
    gf.Set(cos(3*x)*sin(4*y))
    
    gfv = gf.vec.FV().NumPy()[:]
    gfvs.append(gfv)
    
    with open("mesh_test","wb") as file:
        pickle.dump(mesh,file)
    del mesh
    with open("mesh_test","rb") as file:
        mesh = pickle.load(file)

print("If feses are the same, this should be zero.")
print(np.linalg.norm(gfvs[0]-gfvs[1]))

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.25…

If feses are the same, this should be zero.
0.0
